In [1]:
#import necessary libraries

import numpy as np
from pandas import read_csv
import matplotlib.pyplot as plt
from sklearn.metrics import confusion_matrix, ConfusionMatrixDisplay
import copy

In [2]:
#defining activation fucctions

def sigm(x):
    return 1/(1 + np.exp(-x))

def relu(x):
    retArr = np.zeros_like(x)
    retArr[x > 0.0] = x[x > 0.0]
    return retArr

In [3]:
#this is the derivative of a function in terms of the function output

def derivative(y, func):
    if func == sigm:
        return y*(1-y)
    elif func == np.tanh:
        return 1 - y*y
    elif func == relu:
        retArr2 = np.zeros_like(y)
        retArr2[y > 0.0] = 1.0
        return retArr2

In [4]:
def xor_net(inputs, weights, func):
    NOI = len(inputs)
    hiddenLayer = np.zeros((NOI, 2))
    hiddenLayer[:, 0] = func(np.append(inputs, np.ones((NOI, 1)), axis = 1)@weights[0:3])
    hiddenLayer[:, 1] = func(np.append(inputs, np.ones((NOI, 1)), axis = 1)@weights[3:6])
    output = func(np.append(hiddenLayer, np.ones((NOI, 1)), axis = 1)@weights[6:])
    return hiddenLayer, output

In [5]:
def mse(weights, func):
    inputs = np.array([[0, 0], [0, 1], [1, 0], [1, 1]])
    targets = np.array([0, 1, 1, 0])
    hiddenLayer, calcOutput = xor_net(inputs, weights, func)
    return np.sum(0.5*(calcOutput - targets)**2)

In [6]:
def gradmse(weights, func):
    inputs = np.array([[0, 0], [0, 1], [1, 0], [1, 1]])
    targets = np.array([0, 1, 1, 0])
    hiddenLayer, calcOutput = xor_net(inputs, weights, func)
    
    calcGrad = np.zeros(9)
    
    #calcGrad[6] = np.sum((calcOutput - targets)*calcOutput*(1-calcOutput)*hiddenLayer[:, 0])
    #calcGrad[7] = np.sum((calcOutput - targets)*calcOutput*(1-calcOutput)*hiddenLayer[:, 1])
    #calcGrad[8] = np.sum((calcOutput - targets)*calcOutput*(1-calcOutput))
    
    #print((np.append(hiddenLayer, np.ones((4, 1)), axis = 1).T@((calcOutput - targets)*derivative(calcOutput, func))).shape)
    calcGrad[6:] = np.append(hiddenLayer, np.ones((4, 1)), axis = 1).T@((calcOutput - targets)*derivative(calcOutput, func))
    
    #calcGrad[0] = dhl0/dw0*dmse/dhl0
    #calcGrad[0] = np.sum((hiddenLayer[:, 0]*(1 - hiddenLayer[:, 0])*inputs[:, 0])*
    #                     ((calcOutput - targets)*calcOutput*(1-calcOutput)*weights[6]))
    #calcGrad[1] = np.sum((hiddenLayer[:, 0]*(1 - hiddenLayer[:, 0])*inputs[:, 1])*
    #                     ((calcOutput - targets)*calcOutput*(1-calcOutput)*weights[6]))
    #calcGrad[2] = np.sum((hiddenLayer[:, 0]*(1 - hiddenLayer[:, 0]))*
    #                     ((calcOutput - targets)*calcOutput*(1-calcOutput)*weights[6]))
    
    calcGrad[0:3] = (np.append(inputs, np.ones((4, 1)), axis = 1).T@
                     (derivative(hiddenLayer[:, 0], func)*((calcOutput - targets)*derivative(calcOutput, func)*weights[6])))
    
    #calcGrad[3] = np.sum((hiddenLayer[:, 1]*(1 - hiddenLayer[:, 1])*inputs[:, 0])*
    #                     ((calcOutput - targets)*calcOutput*(1-calcOutput)*weights[7]))
    #calcGrad[4] = np.sum((hiddenLayer[:, 1]*(1 - hiddenLayer[:, 1])*inputs[:, 1])*
    #                     ((calcOutput - targets)*calcOutput*(1-calcOutput)*weights[7]))
    #calcGrad[5] = np.sum((hiddenLayer[:, 1]*(1 - hiddenLayer[:, 1]))*
    #                     ((calcOutput - targets)*calcOutput*(1-calcOutput)*weights[7]))
    
    calcGrad[3:6] = (np.append(inputs, np.ones((4, 1)), axis = 1).T@
                     (derivative(hiddenLayer[:, 1], func)*((calcOutput - targets)*derivative(calcOutput, func)*weights[7])))
    
    return calcGrad

In [7]:
#mean = 0, sigma = 1 gaussian initialisation
#eta = 1
#sigmoid activation

weights = np.random.normal(size = 9)
eta = 1
func = sigm

currmse = 2
#prevmse = 0

while True:
    prevmse = copy.deepcopy(currmse)
    currmse = mse(weights, func)
    weights = weights - eta*gradmse(weights, func)
    inputs = np.array([[0, 0], [0, 1], [1, 0], [1, 1]])
    targets = np.array([0, 1, 1, 0])
    hluseless, currOutput = xor_net(inputs, weights, func)
    missClass = 4 - np.sum(np.array(currOutput > 0.5, dtype = int) == targets)
    print('mse is ' + str(currmse) + ' and number of missclassified examples is ' + str(missClass) + 
          ' (with the classified output being ' + str(np.array(currOutput > 0.5, dtype = int)) + ')')
    #if missClass == 0:
    #    break
    if missClass == 0:
        break

mse is 0.5295756680219743 and number of missclassified examples is 2 (with the classified output being [1 1 1 1])
mse is 0.5143137944258752 and number of missclassified examples is 2 (with the classified output being [1 1 1 1])
mse is 0.5077073646709325 and number of missclassified examples is 3 (with the classified output being [1 1 0 1])
mse is 0.5050152784313888 and number of missclassified examples is 2 (with the classified output being [1 1 0 0])
mse is 0.5039147848559504 and number of missclassified examples is 2 (with the classified output being [1 1 0 0])
mse is 0.50343579967068 and number of missclassified examples is 2 (with the classified output being [1 1 0 0])
mse is 0.5031970994996469 and number of missclassified examples is 2 (with the classified output being [1 1 0 0])
mse is 0.5030519596944598 and number of missclassified examples is 2 (with the classified output being [1 1 0 0])
mse is 0.5029442226738877 and number of missclassified examples is 2 (with the classified 

In [8]:
#[-1, 1) uniform initialisation
#eta = 1
#sigmoid activation

weights = np.random.uniform(-1.0, 1.0, 9)
eta = 1
func = sigm

currmse = 2
#prevmse = 0

while True:
    prevmse = copy.deepcopy(currmse)
    currmse = mse(weights, func)
    weights = weights - eta*gradmse(weights, func)
    inputs = np.array([[0, 0], [0, 1], [1, 0], [1, 1]])
    targets = np.array([0, 1, 1, 0])
    hluseless, currOutput = xor_net(inputs, weights, func)
    missClass = 4 - np.sum(np.array(currOutput > 0.5, dtype = int) == targets)
    print('mse is ' + str(currmse) + ' and number of missclassified examples is ' + str(missClass) + 
          ' (with the classified output being ' + str(np.array(currOutput > 0.5, dtype = int)) + ')')
    #if missClass == 0:
    #    break
    if missClass == 0:
        break

mse is 0.52842217003603 and number of missclassified examples is 2 (with the classified output being [1 1 1 1])
mse is 0.5158010693698276 and number of missclassified examples is 2 (with the classified output being [1 1 1 1])
mse is 0.5088333121009838 and number of missclassified examples is 2 (with the classified output being [1 1 1 1])
mse is 0.5051794912220537 and number of missclassified examples is 2 (with the classified output being [1 1 1 1])
mse is 0.5033050450146692 and number of missclassified examples is 2 (with the classified output being [1 1 1 1])
mse is 0.5023403254470169 and number of missclassified examples is 2 (with the classified output being [1 1 1 1])
mse is 0.5018287853761618 and number of missclassified examples is 3 (with the classified output being [1 1 0 1])
mse is 0.501540095611333 and number of missclassified examples is 3 (with the classified output being [1 1 0 1])
mse is 0.5013604369128438 and number of missclassified examples is 2 (with the classified o

In [21]:
#glorot initialisation
#eta = 1
#sigmoid activation

weights = np.append(np.random.normal(0, 1/np.sqrt(2), 6), np.random.normal(0, 1/np.sqrt(1.5), 3))
eta = 1
func = sigm

currmse = 2
#prevmse = 0

while True:
    prevmse = copy.deepcopy(currmse)
    currmse = mse(weights, func)
    weights = weights - eta*gradmse(weights, func)
    inputs = np.array([[0, 0], [0, 1], [1, 0], [1, 1]])
    targets = np.array([0, 1, 1, 0])
    hluseless, currOutput = xor_net(inputs, weights, func)
    missClass = 4 - np.sum(np.array(currOutput > 0.5, dtype = int) == targets)
    print('mse is ' + str(currmse) + ' and number of missclassified examples is ' + str(missClass) + 
          ' (with the classified output being ' + str(np.array(currOutput > 0.5, dtype = int)) + ')')
    #if missClass == 0:
    #    break
    if missClass == 0:
        break

mse is 0.6066418221793304 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
mse is 0.5706666897565494 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
mse is 0.5430573148394829 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
mse is 0.5244087092801725 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
mse is 0.5130832832059479 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
mse is 0.5067076515889591 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
mse is 0.5032848202564655 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
mse is 0.5014948931155718 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
mse is 0.5005697396915522 and number of missclassified examples is 2 (with the classifie

In [18]:
#glorot initialisation
#eta = 0.5
#sigmoid activation

weights = np.append(np.random.normal(0, 1/np.sqrt(2), 6), np.random.normal(0, 1/np.sqrt(1.5), 3))
eta = 0.5
func = sigm

currmse = 2
#prevmse = 0

while True:
    prevmse = copy.deepcopy(currmse)
    currmse = mse(weights, func)
    weights = weights - eta*gradmse(weights, func)
    inputs = np.array([[0, 0], [0, 1], [1, 0], [1, 1]])
    targets = np.array([0, 1, 1, 0])
    hluseless, currOutput = xor_net(inputs, weights, func)
    missClass = 4 - np.sum(np.array(currOutput > 0.5, dtype = int) == targets)
    print('mse is ' + str(currmse) + ' and number of missclassified examples is ' + str(missClass) + 
          ' (with the classified output being ' + str(np.array(currOutput > 0.5, dtype = int)) + ')')
    #if missClass == 0:
    #    break
    if missClass == 0:
        break

mse is 0.5333994443027957 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
mse is 0.5235166308713187 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
mse is 0.5164198352712716 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
mse is 0.5114580233013406 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
mse is 0.5080558890642708 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
mse is 0.5057543889942766 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
mse is 0.5042107457783916 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
mse is 0.5031800537625871 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
mse is 0.5024924523178916 and number of missclassified examples is 3 (with the classifie

In [19]:
#glorot initialisation
#eta = 0.1
#sigmoid activation

weights = np.append(np.random.normal(0, 1/np.sqrt(2), 6), np.random.normal(0, 1/np.sqrt(1.5), 3))
eta = 0.1
func = sigm

currmse = 2
#prevmse = 0

while True:
    prevmse = copy.deepcopy(currmse)
    currmse = mse(weights, func)
    weights = weights - eta*gradmse(weights, func)
    inputs = np.array([[0, 0], [0, 1], [1, 0], [1, 1]])
    targets = np.array([0, 1, 1, 0])
    hluseless, currOutput = xor_net(inputs, weights, func)
    missClass = 4 - np.sum(np.array(currOutput > 0.5, dtype = int) == targets)
    print('mse is ' + str(currmse) + ' and number of missclassified examples is ' + str(missClass) + 
          ' (with the classified output being ' + str(np.array(currOutput > 0.5, dtype = int)) + ')')
    #if missClass == 0:
    #    break
    if missClass == 0:
        break

mse is 0.5407511839656479 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
mse is 0.5379863354375793 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
mse is 0.535383693921216 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
mse is 0.5329373420645516 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
mse is 0.5306410904832422 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
mse is 0.5284885578713034 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
mse is 0.5264732441757665 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
mse is 0.5245885964457989 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
mse is 0.5228280672057519 and number of missclassified examples is 2 (with the classified

mse is 0.4995390608885617 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.49953730391497486 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.4995355437593706 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.49953378041134955 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.499532013860478 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.49953024409628777 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.4995284711082754 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.49952669488590284 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.49952491541859706 and number of missclassified examples is 2 (with the class

mse is 0.4966755655618099 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.4966659047615034 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.49665621367572055 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.4966464922032374 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.49663674024254356 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.49662695769184273 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.4966171444490526 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.49660730041180356 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.4965974254774395 and number of missclassified examples is 2 (with the class

mse is 0.47767549157341005 and number of missclassified examples is 1 (with the classified output being [0 1 1 1])
mse is 0.47761784265064966 and number of missclassified examples is 1 (with the classified output being [0 1 1 1])
mse is 0.47756008860182986 and number of missclassified examples is 1 (with the classified output being [0 1 1 1])
mse is 0.4775022294279003 and number of missclassified examples is 1 (with the classified output being [0 1 1 1])
mse is 0.4774442651303864 and number of missclassified examples is 1 (with the classified output being [0 1 1 1])
mse is 0.4773861957113893 and number of missclassified examples is 1 (with the classified output being [0 1 1 1])
mse is 0.47732802117358597 and number of missclassified examples is 1 (with the classified output being [0 1 1 1])
mse is 0.47726974152022866 and number of missclassified examples is 1 (with the classified output being [0 1 1 1])
mse is 0.4772113567551451 and number of missclassified examples is 1 (with the clas

mse is 0.42303414991639776 and number of missclassified examples is 1 (with the classified output being [0 1 1 1])
mse is 0.42293949976708667 and number of missclassified examples is 1 (with the classified output being [0 1 1 1])
mse is 0.4228448834063854 and number of missclassified examples is 1 (with the classified output being [0 1 1 1])
mse is 0.42275030112513046 and number of missclassified examples is 1 (with the classified output being [0 1 1 1])
mse is 0.4226557532132834 and number of missclassified examples is 1 (with the classified output being [0 1 1 1])
mse is 0.4225612399599253 and number of missclassified examples is 1 (with the classified output being [0 1 1 1])
mse is 0.4224667616532526 and number of missclassified examples is 1 (with the classified output being [0 1 1 1])
mse is 0.4223723185805718 and number of missclassified examples is 1 (with the classified output being [0 1 1 1])
mse is 0.4222779110282946 and number of missclassified examples is 1 (with the classi

mse is 0.37742470702253805 and number of missclassified examples is 1 (with the classified output being [0 1 1 1])
mse is 0.3773665857838192 and number of missclassified examples is 1 (with the classified output being [0 1 1 1])
mse is 0.3773085090578624 and number of missclassified examples is 1 (with the classified output being [0 1 1 1])
mse is 0.3772504767164627 and number of missclassified examples is 1 (with the classified output being [0 1 1 1])
mse is 0.3771924886313893 and number of missclassified examples is 1 (with the classified output being [0 1 1 1])
mse is 0.3771345446743868 and number of missclassified examples is 1 (with the classified output being [0 1 1 1])
mse is 0.3770766447171768 and number of missclassified examples is 1 (with the classified output being [0 1 1 1])
mse is 0.37701878863145843 and number of missclassified examples is 1 (with the classified output being [0 1 1 1])
mse is 0.3769609762889107 and number of missclassified examples is 1 (with the classif

mse is 0.33801445603277586 and number of missclassified examples is 1 (with the classified output being [0 1 1 1])
mse is 0.3379551451924751 and number of missclassified examples is 1 (with the classified output being [0 1 1 1])
mse is 0.33789577994733744 and number of missclassified examples is 1 (with the classified output being [0 1 1 1])
mse is 0.33783636008986384 and number of missclassified examples is 1 (with the classified output being [0 1 1 1])
mse is 0.337776885411952 and number of missclassified examples is 1 (with the classified output being [0 1 1 1])
mse is 0.337717355704893 and number of missclassified examples is 1 (with the classified output being [0 1 1 1])
mse is 0.3376577707593682 and number of missclassified examples is 1 (with the classified output being [0 1 1 1])
mse is 0.33759813036544617 and number of missclassified examples is 1 (with the classified output being [0 1 1 1])
mse is 0.33753843431257846 and number of missclassified examples is 1 (with the classi

mse is 0.2534841697499759 and number of missclassified examples is 1 (with the classified output being [0 1 1 1])
mse is 0.2532625942374359 and number of missclassified examples is 1 (with the classified output being [0 1 1 1])
mse is 0.2530406919800088 and number of missclassified examples is 1 (with the classified output being [0 1 1 1])
mse is 0.25281846415809606 and number of missclassified examples is 1 (with the classified output being [0 1 1 1])
mse is 0.2525959119615303 and number of missclassified examples is 1 (with the classified output being [0 1 1 1])
mse is 0.25237303658950777 and number of missclassified examples is 1 (with the classified output being [0 1 1 1])
mse is 0.2521498392505228 and number of missclassified examples is 1 (with the classified output being [0 1 1 1])
mse is 0.2519263211622982 and number of missclassified examples is 1 (with the classified output being [0 1 1 1])
mse is 0.251702483551718 and number of missclassified examples is 1 (with the classifi

In [26]:
#trying to find a set of weights through a random search

for idx1 in range(10):
    counter = 0
    while True:
        counter = counter + 1
        weights = np.random.uniform(-2.0, 2.0, 9)
        inputs = np.array([[0, 0], [0, 1], [1, 0], [1, 1]])
        targets = np.array([0, 1, 1, 0])
        hluseless, currOutput = xor_net(inputs, weights, func)
        missClass = 4 - np.sum(np.array(currOutput > 0.5, dtype = int) == targets)
        if missClass == 0:
            break
    print('In try no. ' + str(idx1+1) + ', ' + str(counter) + ' sets of weights were tried')

In try no. 1, 1966 sets of weights were tried
In try no. 2, 472 sets of weights were tried
In try no. 3, 100 sets of weights were tried
In try no. 4, 1435 sets of weights were tried
In try no. 5, 3701 sets of weights were tried
In try no. 6, 995 sets of weights were tried
In try no. 7, 1509 sets of weights were tried
In try no. 8, 548 sets of weights were tried
In try no. 9, 3189 sets of weights were tried
In try no. 10, 1118 sets of weights were tried


In [158]:
#glorot initialisation
#eta = 0.1
#tanh activation

weights = np.append(np.random.normal(0, 1/np.sqrt(2), 6), np.random.normal(0, 1/np.sqrt(1.5), 3))
eta = 0.1
func = np.tanh

currmse = 2
#prevmse = 0

while True:
    prevmse = copy.deepcopy(currmse)
    currmse = mse(weights, func)
    weights = weights - eta*gradmse(weights, func)
    inputs = np.array([[0, 0], [0, 1], [1, 0], [1, 1]])
    targets = np.array([0, 1, 1, 0])
    hluseless, currOutput = xor_net(inputs, weights, func)
    missClass = 4 - np.sum(np.array(currOutput > 0.5, dtype = int) == targets)
    print('mse is ' + str(currmse) + ' and number of missclassified examples is ' + str(missClass) + 
          ' (with the classified output being ' + str(np.array(currOutput > 0.5, dtype = int)) + ')')
    #if missClass == 0:
    #    break
    if missClass == 0:
        break

mse is 0.9478317335554209 and number of missclassified examples is 2 (with the classified output being [1 1 1 1])
mse is 0.945612272690676 and number of missclassified examples is 2 (with the classified output being [1 1 1 1])
mse is 0.9432168698141243 and number of missclassified examples is 2 (with the classified output being [1 1 1 1])
mse is 0.9406253697565057 and number of missclassified examples is 2 (with the classified output being [1 1 1 1])
mse is 0.9378146281731745 and number of missclassified examples is 2 (with the classified output being [1 1 1 1])
mse is 0.9347579754015365 and number of missclassified examples is 2 (with the classified output being [1 1 1 1])
mse is 0.9314245703990898 and number of missclassified examples is 2 (with the classified output being [1 1 1 1])
mse is 0.9277786206793557 and number of missclassified examples is 2 (with the classified output being [1 1 1 1])
mse is 0.923778439234396 and number of missclassified examples is 2 (with the classified 

mse is 0.26357712602006167 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.2635524096158983 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.26352777887194334 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.26350323335541004 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.26347877263636565 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.2634543962877093 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.2634301038851482 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.2634058950071752 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.2633817692350468 and number of missclassified examples is 2 (with the class

mse is 0.25579388986876395 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.2557890900953796 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.25578429803131614 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.2557795136582929 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.25577473695808617 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.25576996791252954 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.25576520650351275 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.25576045271298253 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.25575570652294194 and number of missclassified examples is 2 (with the cl

mse is 0.2533996380863729 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.25339793739232574 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.2533962383584717 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.253394540982409 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.25339284526173966 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.25339115119407096 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.2533894587770146 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.2533877680081863 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.2533860788852071 and number of missclassified examples is 2 (with the classif

mse is 0.2523797063219898 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.2523788595162001 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.2523780133002813 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.2523771676736227 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.2523763226356152 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.25237547818565026 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.25237463432312024 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.25237379104741847 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.2523729483579388 and number of missclassified examples is 2 (with the classi

...

mse is 0.2502939957364808 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.25029398195242414 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.2502939681696451 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.25029395438814395 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.2502939406079203 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.2502939268289739 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.25029391305130494 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.25029389927491286 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.25029388549979775 and number of missclassified examples is 2 (with the clas

mse is 0.25028277407312477 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.2502827613100851 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.25028274854818433 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.25028273578742277 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.2502827230278002 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.25028271026931626 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.25028269751197096 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.2502826847557641 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.25028267200069576 and number of missclassified examples is 2 (with the cla

mse is 0.2502724994476725 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.25027248758550336 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.2502724757243554 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.25027246386422886 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.250272452005123 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.25027244014703814 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.2502724282899741 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.2502724164339306 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.25027240457890765 and number of missclassified examples is 2 (with the classi

mse is 0.2502625185144538 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.25026250749626444 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.25026249647899 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.2502624854626302 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.25026247444718475 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.25026246343265374 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.25026245241903683 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.25026244140633425 and number of missclassified examples is 2 (with the classified output being [0 0 1 1])
mse is 0.25026243039454565 and number of missclassified examples is 2 (with the class

KeyboardInterrupt: 

In [24]:
#he initialisation
#eta = 1
#relu activation

weights = np.random.normal(size = 9)
print('Initial weights are ' + str(weights))
eta = 1
func = relu

currmse = 2
#prevmse = 0

while True:
    prevmse = copy.deepcopy(currmse)
    currmse = mse(weights, func)
    weights = weights - eta*gradmse(weights, func)
    print('New weights are ' + str(weights))
    inputs = np.array([[0, 0], [0, 1], [1, 0], [1, 1]])
    targets = np.array([0, 1, 1, 0])
    hluseless, currOutput = xor_net(inputs, weights, func)
    missClass = 4 - np.sum(np.array(currOutput > 0.0, dtype = int) == targets)
    print('mse is ' + str(currmse) + ' and number of missclassified examples is ' + str(missClass) + 
          ' (with the classified output being ' + str(np.array(currOutput > 0.5, dtype = int)) + ')')
    #if missClass == 0:
    #    break
    if missClass == 0:
        break

Initial weights are [-0.32751119  0.60287235  3.72635544 -2.2847943  -1.08590443 -1.20876116
 -1.08583758 -0.79397352  0.50465837]
New weights are [-0.32751119  0.60287235  3.72635544 -2.2847943  -1.08590443 -1.20876116
 -1.08583758 -0.79397352  0.50465837]
mse is 1.0 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
New weights are [-0.32751119  0.60287235  3.72635544 -2.2847943  -1.08590443 -1.20876116
 -1.08583758 -0.79397352  0.50465837]
mse is 1.0 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
New weights are [-0.32751119  0.60287235  3.72635544 -2.2847943  -1.08590443 -1.20876116
 -1.08583758 -0.79397352  0.50465837]
mse is 1.0 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
New weights are [-0.32751119  0.60287235  3.72635544 -2.2847943  -1.08590443 -1.20876116
 -1.08583758 -0.79397352  0.50465837]
mse is 1.0 and number of missclassified examples is 2 (with the 

New weights are [-0.32751119  0.60287235  3.72635544 -2.2847943  -1.08590443 -1.20876116
 -1.08583758 -0.79397352  0.50465837]
mse is 1.0 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
New weights are [-0.32751119  0.60287235  3.72635544 -2.2847943  -1.08590443 -1.20876116
 -1.08583758 -0.79397352  0.50465837]
mse is 1.0 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
New weights are [-0.32751119  0.60287235  3.72635544 -2.2847943  -1.08590443 -1.20876116
 -1.08583758 -0.79397352  0.50465837]
mse is 1.0 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
New weights are [-0.32751119  0.60287235  3.72635544 -2.2847943  -1.08590443 -1.20876116
 -1.08583758 -0.79397352  0.50465837]
mse is 1.0 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
New weights are [-0.32751119  0.60287235  3.72635544 -2.2847943  -1.08590443 -1.20876116
 -1.085

New weights are [-0.32751119  0.60287235  3.72635544 -2.2847943  -1.08590443 -1.20876116
 -1.08583758 -0.79397352  0.50465837]
mse is 1.0 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
New weights are [-0.32751119  0.60287235  3.72635544 -2.2847943  -1.08590443 -1.20876116
 -1.08583758 -0.79397352  0.50465837]
mse is 1.0 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
New weights are [-0.32751119  0.60287235  3.72635544 -2.2847943  -1.08590443 -1.20876116
 -1.08583758 -0.79397352  0.50465837]
mse is 1.0 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
New weights are [-0.32751119  0.60287235  3.72635544 -2.2847943  -1.08590443 -1.20876116
 -1.08583758 -0.79397352  0.50465837]
mse is 1.0 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
New weights are [-0.32751119  0.60287235  3.72635544 -2.2847943  -1.08590443 -1.20876116
 -1.085

mse is 1.0 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
New weights are [-0.32751119  0.60287235  3.72635544 -2.2847943  -1.08590443 -1.20876116
 -1.08583758 -0.79397352  0.50465837]
mse is 1.0 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
New weights are [-0.32751119  0.60287235  3.72635544 -2.2847943  -1.08590443 -1.20876116
 -1.08583758 -0.79397352  0.50465837]
mse is 1.0 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
New weights are [-0.32751119  0.60287235  3.72635544 -2.2847943  -1.08590443 -1.20876116
 -1.08583758 -0.79397352  0.50465837]
mse is 1.0 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
New weights are [-0.32751119  0.60287235  3.72635544 -2.2847943  -1.08590443 -1.20876116
 -1.08583758 -0.79397352  0.50465837]
mse is 1.0 and number of missclassified examples is 2 (with the classified output being [0 0 0 0

New weights are [-0.32751119  0.60287235  3.72635544 -2.2847943  -1.08590443 -1.20876116
 -1.08583758 -0.79397352  0.50465837]
mse is 1.0 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
New weights are [-0.32751119  0.60287235  3.72635544 -2.2847943  -1.08590443 -1.20876116
 -1.08583758 -0.79397352  0.50465837]
mse is 1.0 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
New weights are [-0.32751119  0.60287235  3.72635544 -2.2847943  -1.08590443 -1.20876116
 -1.08583758 -0.79397352  0.50465837]
mse is 1.0 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
New weights are [-0.32751119  0.60287235  3.72635544 -2.2847943  -1.08590443 -1.20876116
 -1.08583758 -0.79397352  0.50465837]
mse is 1.0 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
New weights are [-0.32751119  0.60287235  3.72635544 -2.2847943  -1.08590443 -1.20876116
 -1.085

mse is 1.0 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
New weights are [-0.32751119  0.60287235  3.72635544 -2.2847943  -1.08590443 -1.20876116
 -1.08583758 -0.79397352  0.50465837]
mse is 1.0 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
New weights are [-0.32751119  0.60287235  3.72635544 -2.2847943  -1.08590443 -1.20876116
 -1.08583758 -0.79397352  0.50465837]
mse is 1.0 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
New weights are [-0.32751119  0.60287235  3.72635544 -2.2847943  -1.08590443 -1.20876116
 -1.08583758 -0.79397352  0.50465837]
mse is 1.0 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
New weights are [-0.32751119  0.60287235  3.72635544 -2.2847943  -1.08590443 -1.20876116
 -1.08583758 -0.79397352  0.50465837]
mse is 1.0 and number of missclassified examples is 2 (with the classified output being [0 0 0 0

New weights are [-0.32751119  0.60287235  3.72635544 -2.2847943  -1.08590443 -1.20876116
 -1.08583758 -0.79397352  0.50465837]
mse is 1.0 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
New weights are [-0.32751119  0.60287235  3.72635544 -2.2847943  -1.08590443 -1.20876116
 -1.08583758 -0.79397352  0.50465837]
mse is 1.0 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
New weights are [-0.32751119  0.60287235  3.72635544 -2.2847943  -1.08590443 -1.20876116
 -1.08583758 -0.79397352  0.50465837]
mse is 1.0 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
New weights are [-0.32751119  0.60287235  3.72635544 -2.2847943  -1.08590443 -1.20876116
 -1.08583758 -0.79397352  0.50465837]
mse is 1.0 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
New weights are [-0.32751119  0.60287235  3.72635544 -2.2847943  -1.08590443 -1.20876116
 -1.085

New weights are [-0.32751119  0.60287235  3.72635544 -2.2847943  -1.08590443 -1.20876116
 -1.08583758 -0.79397352  0.50465837]
mse is 1.0 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
New weights are [-0.32751119  0.60287235  3.72635544 -2.2847943  -1.08590443 -1.20876116
 -1.08583758 -0.79397352  0.50465837]
mse is 1.0 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
New weights are [-0.32751119  0.60287235  3.72635544 -2.2847943  -1.08590443 -1.20876116
 -1.08583758 -0.79397352  0.50465837]
mse is 1.0 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
New weights are [-0.32751119  0.60287235  3.72635544 -2.2847943  -1.08590443 -1.20876116
 -1.08583758 -0.79397352  0.50465837]
mse is 1.0 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
New weights are [-0.32751119  0.60287235  3.72635544 -2.2847943  -1.08590443 -1.20876116
 -1.085

mse is 1.0 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
New weights are [-0.32751119  0.60287235  3.72635544 -2.2847943  -1.08590443 -1.20876116
 -1.08583758 -0.79397352  0.50465837]
mse is 1.0 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
New weights are [-0.32751119  0.60287235  3.72635544 -2.2847943  -1.08590443 -1.20876116
 -1.08583758 -0.79397352  0.50465837]
mse is 1.0 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
New weights are [-0.32751119  0.60287235  3.72635544 -2.2847943  -1.08590443 -1.20876116
 -1.08583758 -0.79397352  0.50465837]
mse is 1.0 and number of missclassified examples is 2 (with the classified output being [0 0 0 0])
New weights are [-0.32751119  0.60287235  3.72635544 -2.2847943  -1.08590443 -1.20876116
 -1.08583758 -0.79397352  0.50465837]
mse is 1.0 and number of missclassified examples is 2 (with the classified output being [0 0 0 0

KeyboardInterrupt: 